<font size=7>Getting Started with SingleR</font>

This is my first notebook playin with single R. Lets see what I can do!

Load in the package:

In [42]:
library(SingleR)

# Load SingleR Files <small><font color="orange">Error in SingleR.References.R</font></small>

Files to Add:
``` python
HelperFunctions.R  SingleR.Create.R  SingleR.Object.R  SingleR.Plotting.R  SingleR.R  SingleR.References.R
```


In [43]:
source("/home/jovyan/Public/SingleR/R/HelperFunctions.R")

In [44]:
source("/home/jovyan/Public/SingleR/R/SingleR.Create.R")

In [45]:
source("/home/jovyan/Public/SingleR/R/SingleR.Object.R")

In [46]:
source("/home/jovyan/Public/SingleR/R/SingleR.Plotting.R")

In [47]:
source("/home/jovyan/Public/SingleR/R/SingleR.R")

In [48]:
library(parallel)

In [49]:
library(RColorBrewer)

In [50]:
source("/home/jovyan/Public/SingleR/R/SingleR.References.R")

# Load in CreateSinglerSeuratObject <font color="red">Trying to fix glitch</font>

In [56]:
CreateSinglerSeuratObject = function(counts,annot=NULL,project.name,
                                     min.genes=200,technology='10X',
                                     species='Human',citation='',
                                     ref.list=list(),normalize.gene.length=F,
                                     variable.genes='de',fine.tune=T,
                                     reduce.file.size=T,do.signatures=F,
                                     min.cells=2,npca=10,regress.out='nUMI',
                                     do.main.types=T,reduce.seurat.object=T,
                                     temp.dir=NULL, numCores = SingleR.numCores) {
  if (!requireNamespace("Seurat", quietly = TRUE)) {
    stop("Seurat needed for this function to work. Please install it.",
         call. = FALSE)
  }
  
  print(project.name)
  print('Reading single-cell data...')
  sc.data = ReadSingleCellData(counts,annot)
  print('Create Seurat object...')
  seurat = SingleR.CreateSeurat(project.name,sc.data$counts,min.genes=
                                  min.genes,min.cells=min.cells,
                                regress.out=regress.out,npca=npca,
                                temp.dir=temp.dir)
  if (packageVersion('Seurat')>=3) {
    data = seurat@assays$RNA@data
    clusters = seurat@active.ident
  } else {
    data = seurat@data
    clusters = seurat@ident
    
  }
  
  orig.ident = sc.data$orig.ident[colnames(data)]
  counts = as.matrix(sc.data$counts[,colnames(data)])
  
  seurat@meta.data$orig.ident = factor(orig.ident)
  
  if(reduce.seurat.object==T) {
    if (packageVersion('Seurat')>=3) {
      seurat@assays$RNA@counts = matrix()
      seurat@assays$RNA@scale.data = matrix()
    } else {
      seurat@raw.data = c()
      seurat@scale.data = c()
      seurat@calc.params = list()
    }
  }
  
  print('Creat SingleR object...')
  
  singler = CreateSinglerObject(counts,orig.ident,project.name,
                                min.genes=min.genes,technology,species,
                                citation,ref.list,
                                normalize.gene.length,variable.genes,
                                fine.tune,do.signatures,
                                clusters,do.main.types,
                                reduce.file.size,temp.dir,numCores = numCores)
  
  singler$seurat = seurat 
  
  if (packageVersion('Seurat')>=3) {
    singler$meta.data$xy = seurat@reductions$tsne@cell.embeddings
    singler$meta.data$clusters = seurat@active.ident
    
  } else {
    singler$meta.data$xy = seurat@dr$tsne@cell.embeddings
    singler$meta.data$clusters = seurat@ident
  }
  singler
}

# Download SingleR

In [22]:
library(devtools)

In [23]:
devtools::install_github('dviraran/SingleR')

fs        (1.2.7  -> 1.3.1 ) [CRAN]
future    (1.12.0 -> 1.13.0) [CRAN]
ggrepel   (0.8.0  -> 0.8.1 ) [CRAN]
pillar    (1.3.1  -> 1.4.0 ) [CRAN]
processx  (3.3.0  -> 3.3.1 ) [CRAN]
rcmdcheck (1.3.2  -> 1.3.3 ) [CRAN]
vctrs     (NA     -> 0.1.0 ) [CRAN]
zeallot   (NA     -> 0.1.0 ) [CRAN]


Installing 8 packages: fs, future, ggrepel, pillar, processx, rcmdcheck, vctrs, zeallot
Updating HTML index of packages in '.Library'
Making 'packages.html' ... done
Warning message in get0(oNam, envir = ns):
“internal error -3 in R_decompress1”

ERROR: Error in get0(oNam, envir = ns): lazy-load database '/opt/conda/lib/R/library/processx/R/processx.rdb' is corrupt


# Do some data cleaning

## Read Counts File

We load in the RNA "Counts" data files. We will have to remove the duplicate counts from the data file

In [4]:
data = read.table('GSE74923_old.txt', sep="\t", header=TRUE)

In [5]:
dim(data)

[1] 23420   195

In [6]:
data[1:10,1:10]

X        L1210_1 L1210_2 L1210_3 L1210_4 L1210_5 L1210_6 L1210_7 L1210_8
1  Itm2a      0.00    0.00    0.00    0.00    0.00    0.00    0.00   0     
2  Sergef    33.01    9.70   60.20   17.12    2.39   33.71   44.70   0     
3  Fam109a   14.01    0.00   46.77   13.91   36.47    5.61    0.00   0     
4  Dhx9      20.41   32.99    5.64   14.66   36.90   24.11   40.52  99     
5  Ssu72    171.92  156.27  112.83  178.06  125.24  132.66  169.59   0     
6  Olfr1018   0.00    0.00    0.00    0.00    0.00    0.00    0.00   0     
7  Fam71e2    0.00    0.00    0.00    0.00    0.00    0.00    0.00   0     
8  Eif2b2   106.05   58.25   63.25  102.77   92.82  164.20   95.26   0     
9  Mks1      10.37    0.00    0.00   17.16    2.88    0.00    0.00   0     
10 Hebp2      0.00    0.00    0.00    0.00    0.00    0.00    0.00   0     
   L1210_9
1    0.00 
2   19.92 
3   13.49 
4   50.82 
5  113.62 
6    0.00 
7    0.00 
8   87.90 
9    0.00 
10   0.00

## Read types file

We check to make sure that the "types" data file is the right shape

In [7]:
data2 = read.table('GSE74923_annotations.txt', sep="\t", header=TRUE)

In [8]:
dim(data)

[1] 23420   195

## Remove Duplicates from Counts

In [ ]:
dataNew = data[!duplicated(data$X), ]

In [ ]:
dim(dataNew)

In [ ]:
row.names(dataNew)= as.character(dataNew$X)

In [ ]:
dataNew$X = NULL

We check that everything looks good

In [ ]:
dataNew[1:10,1:10]

## See Format of GSE74923_old.txt

We have to make sure that the format of our file is the same as the old file, `GSE74923_old.txt`. Lets take a look at what the old file looks like

In [ ]:
con <- file("GSE74923_old.txt","r")
first_lines <- readLines(con,n=3)
close(con)

In [ ]:
class(first_lines)

In [ ]:
length(first_lines)

We look at the first row of `GSE74923_old.txt` aka, the header.

In [ ]:
print(first_lines[1])

We look at the first row of real data in `GSE74923_old.txt`

In [ ]:
print(first_lines[2])

## Create GSE74923_new.txt


We save the our corrected version of the dataset to `GSE74923_new.txt`

<font color="orange">Note: We comment out the line where we save the data. Remove the comment if you want to resave data.</font>

In [ ]:
#write.table( dataNew, "GSE74923_new.txt", sep = "\t" )

In [ ]:
con <- file("GSE74923_new.txt","r")
first_lines <- readLines(con,n=2)
close(con)

We then check that the text file we created is formatted correctly (compare to results from last section)

In [ ]:
print(first_lines[1])

In [ ]:
print(first_lines[2])

Lets load the data back in to check that everything looks good

In [ ]:
dataCheck = read.table('GSE74923_new.txt', sep="\t", header=TRUE)

In [ ]:
dataCheck[1:10,1:10]

## Create GSE74923_new2.txt

The first try didn't work so lets try again to formatting the data again

In [ ]:
dataNew2 = data[!duplicated(data$X), ]

<font color="orange">Note: We comment out the line where we save the data. Remove the comment if you want to resave data.</font>

In [ ]:
#write.table( dataNew2, "GSE74923_new2.txt", sep = "\t" )

Now we load in the file we created and check to see what it looks like

In [ ]:
dataCheck2 = read.table('GSE74923_new2.txt', sep="\t", header=TRUE)

In [ ]:
dataCheck2[1:10,1:10]

# Test SingleR <font color="orange">(Long Way)</font>

The <font color="blue">SingleR</font> package is causing a bunch of errors. It's debug time! We are going to run the software the long way, line by line. 

We start by disecting the function `CreateSinglerSeuratObject` and running each of it's commands line by line.

In [19]:
annot.file = 'GSE74923_annotations.txt'
counts.file =  'GSE74923_new.txt' 

## <font color="red">Glitch Locations</font>


**Glitch 1**

Checkout out Seurat Object <font color="orange">LONG WAY</font> section.  It shows a glitch in the [SingleR.CreateSeurat](https://github.com/dviraran/SingleR/blob/master/R/SingleR.Create.R) function. 
* Glitch: the `min.genes` function need a dummy assignment to avoid an error.



In [ ]:
checkit.CreateSeurat

## Dissect `CreateSinglerSeuratObject`

The code for the `CreateSinglerSeuratObject` was copied from this location on [Github](https://github.com/dviraran/SingleR/blob/master/R/SingleR.Create.R)

### Set up initial variables

Below are the user inputted variables

In [ ]:
counts = 'GSE74923_new.txt' 
annot =  'GSE74923_new.txt'
project.name = 'GSE74923'

In [ ]:
variable.genes='de'; regress.out='nUMI' 
technology='C1'; species='Mouse'
citation='Kimmerling et al.'; reduce.file.size = F 
normalize.gene.length = T

We now add the default variables

In [ ]:

min.genes=200; 
ref.list=list()
variable.genes='de'; fine.tune=T
do.signatures=F
min.cells=2; npca=10
do.main.types=T; reduce.seurat.object=T
temp.dir=NULL; numCores = SingleR.numCores

### Read Data

In [ ]:
if (!requireNamespace("Seurat", quietly = TRUE)) {
stop("Seurat needed for this function to work. Please install it.",
     call. = FALSE)
}


In [ ]:
print(project.name)

In [ ]:
print('Reading single-cell data...')

In [ ]:
sc.data = ReadSingleCellData(counts,annot)

###  Seurat Object <font color="orange">LONG WAY</font>

This funciton has an error so we are going to run it the long way. At the end remember to set:
```

```


In [ ]:
checkit.CreateSeurat <- function(project.name,sc.data,min.genes = 200,
                                 min.cells = 2,regress.out = 'nUMI',
                                 npca = 10,resolution=0.8,temp.dir=NULL) {
  #fakey=min.genes
  if (!requireNamespace("Seurat", quietly = TRUE)) {
    stop("Seurat needed for this function to work. Please install it.",
         call. = FALSE)
  }
  
  mtgenes = '^mt-'
  
  if (packageVersion('Seurat')>3) {
    sc = CreateSeuratObject(sc.data, min.cells = min.cells, 
                            min.features = min.genes, project = project.name)
    mito.features <- grep(pattern = mtgenes, x = rownames(x = sc), value = TRUE,ignore.case=TRUE)
    percent.mito <- Matrix::colSums(x = GetAssayData(object = sc, slot = 'counts')[mito.features, ]) / Matrix::colSums(x = GetAssayData(object = sc, slot = 'counts'))
    
  } else {
    sc = CreateSeuratObject(sc.data, min.cells = min.cells, 
                            min.genes = min.genes, project = project.name)
    mito.genes <- grep(pattern = mtgenes, x = rownames(x = sc@data), 
                       value = TRUE,ignore.case=TRUE)
    percent.mito <- colSums((sc.data[mito.genes, ]))/colSums(sc.data)
    
  }
  
  sc <- AddMetaData(object = sc, metadata = percent.mito, 
                    col.name = "percent.mito")
  
  sc <- NormalizeData(object = sc, 
                      normalization.method = "LogNormalize", 
                      scale.factor = 10000)
  
  if (packageVersion('Seurat')>3) {
    sc <- FindVariableFeatures(object = sc, selection.method = 'mean.var.plot', 
                               mean.cutoff = c(0.0125, 3), 
                               dispersion.cutoff = c(0.5, Inf) ,
                               do.contour = F, do.plot = F)
    
    sc <- ScaleData(object = sc,use.umi=T)
    sc <- RunPCA(object = sc, npcs = npca, features = VariableFeatures(object = sc),verbose = FALSE)
    sc <- FindNeighbors(object = sc, dims = 1:npca)
    sc <- FindClusters(object = sc,resolution = resolution)
    if (ncol(sc@assays$RNA@data)<100) {
      sc <- RunTSNE(sc,perplexity=10,dims = 1:npca)
    } else {
      sc <- RunTSNE(sc,dims = 1:npca)
      
    }
  } else {
    sc <- FindVariableGenes(object = sc, mean.function = ExpMean, 
                            dispersion.function = LogVMR, 
                            x.low.cutoff = 0.0125, x.high.cutoff = 3, 
                            y.cutoff = 0.5, do.contour = F, do.plot = F)
    if (!is.null(regress.out)) {
      sc <- ScaleData(object = sc, vars.to.regress = regress.out)
    } else {
      sc <- ScaleData(object = sc)
    }
    sc <- RunPCA(object = sc, pcs.compute = npca, pc.genes = sc@var.genes, do.print = FALSE)
    #PCElbowPlot(object = sc)
    sc <- FindClusters(object = sc, reduction.type = "pca", 
                       dims.use = 1:npca,resolution = resolution, 
                       print.output = 0, save.SNN = F, 
                       temp.file.location = temp.dir)
    if (ncol(sc@data)<100) {
      sc <- RunTSNE(sc, dims.use = 1:npca, do.fast = T,perplexity=10  )
    } else {
      sc <- RunTSNE(sc, dims.use = 1:npca, do.fast = T,check_duplicates = FALSE)
      
    }
  }
  
  sc
}


In [15]:
SingleR.CreateSeurat

function (project.name, sc.data, min.genes = 200, min.cells = 2, 
    regress.out = "nUMI", npca = 10, resolution = 0.8, temp.dir = NULL) 
{
    if (!requireNamespace("Seurat", quietly = TRUE)) {
        stop("Seurat needed for this function to work. Please install it.", 
            call. = FALSE)
    }
    mtgenes = "^mt-"
    if (packageVersion("Seurat") > 3) {
        sc = CreateSeuratObject(sc.data, min.cells = min.cells, 
            min.features = min.genes, project = project.name)
        mito.features <- grep(pattern = mtgenes, x = rownames(x = sc), 
            value = TRUE, ignore.case = TRUE)
        percent.mito <- Matrix::colSums(x = GetAssayData(object = sc, 
            slot = "counts")[mito.features, ])/Matrix::colSums(x = GetAssayData(object = sc, 
            slot = "counts"))
    }
    else {
        sc = CreateSeuratObject(sc.data, min.cells = min.cells, 
            min.genes = min.genes, project = project.name)
        mito.genes <- grep(pattern = mtgenes, x = rownames(x = sc@data), 
            value = TRUE, ignore.case = TRUE)
        percent.mito <- colSums((sc.data[mito.genes, ]))/colSums(sc.data)
    }
    sc <- AddMetaData(object = sc, metadata = percent.mito, col.name = "percent.mito")
    sc <- NormalizeData(object = sc, normalization.method = "LogNormalize", 
        scale.factor = 10000)
    if (packageVersion("Seurat") > 3) {
        sc <- FindVariableFeatures(object = sc, selection.method = "mean.var.plot", 
            mean.cutoff = c(0.0125, 3), dispersion.cutoff = c(0.5, 
                Inf), do.contour = F, do.plot = F)
        sc <- ScaleData(object = sc, use.umi = T)
        sc <- RunPCA(object = sc, npcs = npca, features = VariableFeatures(object = sc), 
            verbose = FALSE)
        sc <- FindNeighbors(object = sc, dims = 1:npca)
        sc <- FindClusters(object = sc, resolution = resolution)
        if (ncol(sc@assays$RNA@data) < 100) {
            sc <- RunTSNE(sc, perplexity = 10, dims = 1:npca)
        }
        else {
            sc <- RunTSNE(sc, dims = 1:npca)
        }
    }
    else {
        sc <- FindVariableGenes(object = sc, mean.function = ExpMean, 
            dispersion.function = LogVMR, x.low.cutoff = 0.0125, 
            x.high.cutoff = 3, y.cutoff = 0.5, do.contour = F, 
            do.plot = F)
        if (!is.null(regress.out)) {
            sc <- ScaleData(object = sc, vars.to.regress = regress.out)
        }
        else {
            sc <- ScaleData(object = sc)
        }
        sc <- RunPCA(object = sc, pcs.compute = npca, pc.genes = sc@var.genes, 
            do.print = FALSE)
        sc <- FindClusters(object = sc, reduction.type = "pca", 
            dims.use = 1:npca, resolution = resolution, print.output = 0, 
            save.SNN = F, temp.file.location = temp.dir)
        if (ncol(sc@data) < 100) {
            sc <- RunTSNE(sc, dims.use = 1:npca, do.fast = T, 
                perplexity = 10)
        }
        else {
            sc <- RunTSNE(sc, dims.use = 1:npca, do.fast = T, 
                check_duplicates = FALSE)
        }
    }
    sc
}
<bytecode: 0x559be61c0b70>
<environment: namespace:SingleR>

In [ ]:
print('Create Seurat object...')

In [ ]:
seurat = checkit.CreateSeurat( project.name, sc.data$counts, min.genes=min.genes, min.cells=min.cells, regress.out=regress.out, npca=npca, temp.dir=temp.dir)

In [ ]:
CreateSeuratObject

In [ ]:
min.genes

In [ ]:
  if (packageVersion('Seurat')>3) {
    data = seurat@assays$RNA@data
    clusters = seurat@active.ident
  } else {
    data = seurat@data
    clusters = seurat@ident
    
  }

In [ ]:
  orig.ident = sc.data$orig.ident[colnames(data)]
  counts = sc.data$counts[,colnames(data)]
  
  seurat@meta.data$orig.ident = factor(orig.ident)

In [ ]:
  if(reduce.seurat.object==T) {
    if (packageVersion('Seurat')>3) {
      seurat@assays$RNA@counts = matrix()
      seurat@assays$RNA@scale.data = matrix()
    } else {
      seurat@raw.data = c()
      seurat@scale.data = c()
      seurat@calc.params = list()
    }
  }
  

### Creat SingleR object

In [ ]:
print('Creat SingleR object...')

In [ ]:
singler = CreateSinglerObject(counts,orig.ident,project.name,
                            min.genes=min.genes,technology,species,
                            citation,ref.list,
                            normalize.gene.length,variable.genes,
                            fine.tune,do.signatures,
                            clusters,do.main.types,
                            reduce.file.size,temp.dir,numCores = numCores)

In [ ]:
singler$seurat = seurat 

In [ ]:
if (packageVersion('Seurat')>3) {
singler$meta.data$xy = seurat@reductions$tsne@cell.embeddings
singler$meta.data$clusters = seurat@active.ident

} else {
singler$meta.data$xy = seurat@dr$tsne@cell.embeddings
singler$meta.data$clusters = seurat@ident
}

In [ ]:
singler


# Test SingleR  <font color="red">Errors</font>

In [54]:
annot.file = 'GSE74923_annotations.txt'
counts.file =  'GSE74923_new.txt' 

In [60]:
library(dplyr)
library(Seurat)


Attaching package: ‘dplyr’

The following objects are masked from ‘package:stats’:

    filter, lag

The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union



``` python
Imports: BiocManager,
    RColorBrewer,
    outliers,
    matrixStats,
    plyr,
    dplyr,
    ggplot2,
    pbmcapply,
    Matrix,
    GSEABase,
    GSVA,
    pheatmap,
    parallel,
    devtools,
    doFuture,
    data.table,
    foreach,
    singscore,
    doParallel
Suggests: Seurat (>= 2.2)
```

In [ ]:
library( BiocManager )
library( RColorBrewer)
library( outliers)
library( matrixStats)
library( plyr)
library( dplyr)
library( ggplot2)
library( pbmcapply)
library( Matrix)
library( GSEABase)
library( GSVA)
library( pheatmap)
library( parallel)
library( devtools)
library( doFuture)
library( data.table)
library( foreach)
library( singscore)
library( doParallel)

In [61]:
singler = CreateSinglerSeuratObject(counts.file, annot.file, 'GSE74923', min.genes=200,
                                    variable.genes='de', regress.out='nUMI', 
                                    technology='C1', species='Mouse',
                                    citation='Kimmerling et al.', reduce.file.size = F, 
                                    normalize.gene.length = T)

[1] "GSE74923"
[1] "Reading single-cell data..."
[1] "Create Seurat object..."


Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 169009.680000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 244511.190000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 199154.110000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 251728.650000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 197656.620000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 228082.300000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 265934.950000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 793381.260000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 134678.160000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 146700.730000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 179659.260000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 205482.760000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 203992.810000”Warning mess

“non-integer x = 16.370000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 36.800000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 15.300000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.880000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 30.020000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3.920000”Warning message in theta.ml(y = y, mu = fit$fitted):
“iteration limit reached”Warning message in sqrt(1/i):
“NaNs produced”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3.830000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2.420000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.720000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 7.600000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 10.380000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 14.800000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 5.

“non-integer x = 2228.960000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2272.010000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2467.870000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2212.850000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2383.140000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1889.280000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2298.020000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2201.550000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2466.080000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3121.520000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 5319.250000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2076.270000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2549.120000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1573.880000”Warning m

“non-integer x = 4613.500000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2757.090000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3446.310000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4512.740000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4897.520000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4224.760000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4298.960000”Warning message in theta.ml(y = y, mu = fit$fitted):
“iteration limit reached”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2364.940000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1956.280000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1825.860000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2394.960000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2259.140000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1976.910000”Warni

...

“non-integer x = 39.670000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 33.920000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 34.200000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 43.570000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 11.010000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 51.060000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 126.040000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 61.430000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4.200000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.870000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 21.020000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 73.690000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2.070000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 41.740000”Warning message in dpois(y, mu, log = T

“non-integer x = 5.080000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 74.650000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 4.210000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 62.730000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 50.920000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 232.670000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 92.440000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 176.420000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 68.740000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 16.340000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 72.070000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 34.160000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 138.830000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 111.500000”Warning message in dpois(y, mu, log

“non-integer x = 8.570000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.200000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.730000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.540000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.840000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.810000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.060000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2.680000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 12.320000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.390000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3.220000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 0.690000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 3.400000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2.950000”Warning message in dpois(y, mu, log = TRUE):
“non-

“non-integer x = 153.120000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 267.010000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 129.500000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 231.260000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 131.630000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 174.890000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2972.430000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 956.360000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 214.900000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 72.950000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 299.420000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 265.710000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 35.320000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 199.460000”Warning message in dpois

“non-integer x = 11.540000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 2.260000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 5.100000”Warning message in dpois(y, mu, log = TRUE):
“non-integer x = 1.250000”IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [63]:
save(singler,file='GSE74923.RData')

ERROR: Error in save(singler, file = "GSE74923.RData"): object ‘singler’ not found


In [64]:
singler

ERROR: Error in eval(expr, envir, enclos): object 'singler' not found


In [ ]:
#save(singler,file='GSE74923.RData'))

In [ ]:
#file.info(counts.file)

In [58]:
CreateSeuratObject

ERROR: Error in eval(expr, envir, enclos): object 'CreateSeuratObject' not found


# Draw Scatter <font color="red">Not Implemented</font>

In [ ]:
#load (file.path(path,'GSE74923.RData'))
#SingleR.DrawScatter(sc_data = singler$seurat@data,cell_id = 10, 
#                    ref = immgen, sample_id = 232)